In [1]:
import os
import glob
import pandas as pd
import numpy as np

# Caminho da pasta com os arquivos Excel
folder_path = r"C:\Users\joao.herculano\Documents\analise de previsao ginseng x mar\promoções"

# Padrão para localizar todos os arquivos .xlsx
excel_files = glob.glob(os.path.join(folder_path, '*.xlsx'))

# Lista para armazenar os DataFrames válidos
dataframes = []

# Colunas obrigatórias
required_columns = ['PDV',
'PRODUTO',
'COMPRA FINAL']

# Para cada arquivo Excel
for file in excel_files:
    success = False
    for header_row in range(10):
        try:
            df = pd.read_excel(file, header=header_row)
            if all(col in df.columns for col in required_columns):
                if 'Sugestão Pedro' in df.columns or 'Sugestão Laura' in df.columns:
                    print(file)
                df = df[required_columns]
                df['arquivo fonte'] = file
                dataframes.append(df)
                success = True
                break
        except Exception as e:
            continue
    if not success:
        print(f"Arquivo ignorado (colunas ausentes ou erro na leitura): {file}")

# Concatena os DataFrames válidos
retorno_analista = pd.concat(dataframes, ignore_index=True)

# Exibe a forma do DataFrame resultante
print(retorno_analista.shape)

(105809, 4)


In [2]:
retorno_analista = retorno_analista.drop_duplicates()
retorno_analista.shape

(105809, 4)

In [3]:
retorno_analista.columns

Index(['PDV', 'PRODUTO', 'COMPRA FINAL', 'arquivo fonte'], dtype='object')

In [4]:
retorno_analista = retorno_analista.fillna(0)
#retorno_analista = retorno_analista[retorno_analista['COMPRA FINAL']!=0]
retorno_analista['COMPRA FINAL'] = retorno_analista['COMPRA FINAL'].astype('Int64')

retorno_analista2 = retorno_analista.groupby(['PDV','PRODUTO','arquivo fonte'])['COMPRA FINAL'].max().reset_index()

In [5]:
retorno_analista2.sort_values('COMPRA FINAL',ascending=False).head()

PDV  PRODUTO                                      arquivo fonte  \
57211  20997    84387  C:\Users\joao.herculano\Documents\analise de p...   
55854  20997    22249  C:\Users\joao.herculano\Documents\analise de p...   
54453  20996    48062  C:\Users\joao.herculano\Documents\analise de p...   
49726  20993    19734  C:\Users\joao.herculano\Documents\analise de p...   
50060  20993    50677  C:\Users\joao.herculano\Documents\analise de p...   

       COMPRA FINAL  
57211          3000  
55854          1600  
54453          1500  
49726          1450  
50060          1450

In [6]:
retorno_analista2['chave'] = retorno_analista2['PDV'].astype('str')+retorno_analista2['PRODUTO'].astype('str')

retorno_analista2.head()
retorno_analista2 = retorno_analista2[['chave','PDV',	'PRODUTO',	'COMPRA FINAL','arquivo fonte'	]]

retorno_analista2.head()

chave   PDV  PRODUTO  COMPRA FINAL  \
0  35461004  3546     1004             0   
1  35461004  3546     1004             0   
2  35461004  3546     1004             0   
3  35461676  3546     1676             0   
4  35461680  3546     1680             0   

                                       arquivo fonte  
0  C:\Users\joao.herculano\Documents\analise de p...  
1  C:\Users\joao.herculano\Documents\analise de p...  
2  C:\Users\joao.herculano\Documents\analise de p...  
3  C:\Users\joao.herculano\Documents\analise de p...  
4  C:\Users\joao.herculano\Documents\analise de p...

In [7]:
retorno_analista2['chave'] = retorno_analista2['chave'].str.replace('.0','')

retorno_analista2['chave'].head()

0    35461004
1    35461004
2    35461004
3    35461676
4    35461680
Name: chave, dtype: object

In [8]:
retorno_analista2.to_excel(r'C:\Users\joao.herculano\Documents\analise de previsao ginseng x mar\CompiladoPromo.xlsx',index=False)
